In [1]:
import sys
sys.path.append('../')

%reload_ext autoreload
%autoreload 2
%matplotlib notebook
import matplotlib.pyplot as plt
import torch
import numpy as np
import utils.paramUtil as paramUtil
from utils.skeleton import Skeleton
from mylib import get_motion, animate3d, get_SMPL_layer, get6d, coco_bone, t2m_bone, smpl_coco_bone, smpl_smpl_bone, smpl_human36_bone
from utils.motion_process import recover_from_ric, recover_from_rot, recover_root_rot_pos
from pytorch3d.transforms import quaternion_to_axis_angle, matrix_to_axis_angle, rotation_6d_to_matrix, \
quaternion_to_matrix, axis_angle_to_quaternion, axis_angle_to_matrix, matrix_to_axis_angle, matrix_to_rotation_6d
from joints2smpl_lib import Joint2SMPL

Reading ../checkpoints/t2m/t2m_motiondiffuse/opt.txt


### H36M

In [3]:
rest_pose = torch.zeros((1,24,3))
# rest_pose[:,12] = torch.tensor((0,3.14/2,0))
verts, Jtr = get_SMPL_layer(rest_pose.view(1,72), display=False)

joint_regressor_h36 = np.load('/home/epinyoan/git/Pose2Mesh_RELEASE/data/Human36M/J_regressor_h36m_correct.npy').astype(np.float32)
joint_coord_cam = torch.matmul(torch.from_numpy(joint_regressor_h36), verts)
smpl_h36_joints = torch.cat((Jtr[:,:22], joint_coord_cam), axis=1).numpy()

# animate3d(joint_coord_cam.numpy(), coco_bone)
# animate3d(Jtr.numpy())
animate3d(smpl_h36_joints, smpl_human36_bone, first_total_standard=63)

torch.Size([24, 6890])


### SMPL joints + COCO Head

In [4]:
import pickle
smpl_data = pickle.load(open('/home/epinyoan/git/smplpytorch/smplpytorch/native/models/basicmodel_m_lbs_10_207_0_v1.0.0.pkl', 'rb'), encoding='latin1')
smpl_j_regressor = np.array(smpl_data['J_regressor'].toarray()).astype(np.float32)
coco_j_regressor = np.load('/home/epinyoan/git/Pose2Mesh_RELEASE/data/COCO/J_regressor_coco.npy').astype(np.float32)
coco_j_regressor = np.concatenate((coco_j_regressor[:5], smpl_j_regressor[15:16]), axis=0)
coco_head_bone = [(1, 2), (0, 1), (0, 2), (2, 4), (1, 3), (0,5)]
smpl_cocohead_bone = t2m_bone + (np.array(coco_head_bone)+22).tolist()

rest_pose = torch.zeros((1,24,3))
verts, Jtr = get_SMPL_layer(rest_pose.view(1,72), display=False)

joint_coord_cam = torch.matmul(torch.from_numpy(coco_j_regressor), verts)
smpl_coco_joints = torch.cat((Jtr[:,:22], joint_coord_cam), axis=1).numpy()

animate3d(smpl_coco_joints, smpl_cocohead_bone, first_total_standard=63)

torch.Size([24, 6890])


### COCO

In [5]:
rest_pose = torch.zeros((1,24,3))
# rest_pose[:,12] = torch.tensor((0,3.14/2,0))
verts, Jtr = get_SMPL_layer(rest_pose.view(1,72), display=False)

joint_regressor_coco = np.load('/home/epinyoan/git/Pose2Mesh_RELEASE/data/COCO/J_regressor_coco.npy').astype(np.float32)
joint_coord_cam = torch.matmul(torch.from_numpy(joint_regressor_coco), verts)
smpl_coco_joints = torch.cat((Jtr[:,:22], joint_coord_cam), axis=1).numpy()

# animate3d(joint_coord_cam.numpy(), coco_bone)
# animate3d(Jtr.numpy())
animate3d(smpl_coco_joints, smpl_coco_bone, first_total_standard=63)

torch.Size([24, 6890])


### Joint2SMPL

In [194]:
data = torch.from_numpy(get_motion()).float()
joint_dataset = recover_from_ric(data, joints_num=22).numpy()
axis_dataset = matrix_to_axis_angle(rotation_6d_to_matrix(get6d(data)))
axis_dataset = torch.cat((axis_dataset, torch.zeros((120,2,3))), axis=1)[0].view(1,-1)

  0%|          | 0/1000 [00:00<?, ?it/s]

data: torch.Size([120, 263]) r_rot_quat: torch.Size([120, 4])
positions: torch.Size([120, 63])
positions2: torch.Size([120, 21, 3])
positions3: torch.Size([120, 21, 3])
positions4: torch.Size([120, 22, 3])


In [195]:
j2smpl = Joint2SMPL(num_smplify_iters=100)
new_opt_joints, new_opt_vertices = j2smpl.run(axis_dataset, joint_dataset)

/home/epinyoan/git/joints2smpl/smpl_models/
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------
------


In [200]:
origin_joints = joint_dataset[:,:22]
new_joints = new_opt_joints[:,:22].clone().cpu().numpy()
origin_gap = np.expand_dims((origin_joints[:,0] - new_joints[:,0]), axis=1)
new_joints[:,:] += origin_gap

In [205]:
joint_original_forward = np.concatenate((origin_joints, new_joints), axis=1)
animate3d(joint_original_forward, smpl_smpl_bone, first_total_standard=63)

Reading ../checkpoints/t2m/t2m_motiondiffuse/opt.txt


In [204]:
coco_joints = []
for vertex in new_opt_vertices:
    joints = torch.matmul(torch.from_numpy(joint_regressor_coco), vertex.cpu())
    coco_joints.append(joints.unsqueeze(0))
coco_joints = torch.cat(coco_joints, axis=0)
smpl_coco_joints = torch.cat((torch.from_numpy(origin_joints), coco_joints+origin_gap), axis=1).numpy()
animate3d(smpl_coco_joints, smpl_coco_bone, first_total_standard=63)

Reading ../checkpoints/t2m/t2m_motiondiffuse/opt.txt
